<a href="https://colab.research.google.com/github/MarinaOhm/master_thesis/blob/main/MS_Forecasting.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [4]:
!pip install pmdarima
!pip uninstall statsmodels
!pip install statsmodels
!pip install pystan~=2.14
!pip install --no-cache-dir fbprophet
!pip install keras-tuner

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Found existing installation: statsmodels 0.13.5
Uninstalling statsmodels-0.13.5:
  Would remove:
    /usr/local/lib/python3.9/dist-packages/statsmodels-0.13.5.dist-info/*
    /usr/local/lib/python3.9/dist-packages/statsmodels/*
Proceed (Y/n)? y
  Successfully uninstalled statsmodels-0.13.5
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
  Using cached statsmodels-0.13.5-cp39-cp39-manylinux_2_17_x86_64.manylinux2014_x86_64.whl (9.9 MB)


Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [6]:
# Importing libraries
import pandas as pd
import numpy as np
import seaborn as sns
import time
import matplotlib.pyplot as plt
import plotly.express as px
import random
import plotly.graph_objs as go
from plotly.subplots import make_subplots
import os
from datetime import datetime
import math
import warnings
warnings.filterwarnings("ignore")

from statsmodels.graphics.tsaplots import plot_acf
from sklearn.metrics import mean_squared_error, r2_score
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestRegressor, GradientBoostingRegressor, AdaBoostRegressor
from xgboost import XGBRegressor
from sklearn.neural_network import MLPRegressor
import lightgbm as lgb
import statsmodels
from pmdarima.arima import auto_arima
from sklearn.model_selection import TimeSeriesSplit, RandomizedSearchCV
from sklearn.metrics import mean_squared_error
import xgboost as xgb
import fbprophet
from fbprophet import Prophet
import prophet.diagnostics
from prophet.diagnostics import cross_validation
from prophet.diagnostics import performance_metrics
warnings.filterwarnings('ignore')
import logging
logging.getLogger('fbprophet').setLevel(logging.WARNING)
from sklearn.model_selection import KFold
from keras.models import Sequential
from keras.layers import Dense, LSTM
from sklearn.metrics import mean_absolute_percentage_error
from sklearn.preprocessing import MinMaxScaler
import tensorflow as tf
from tensorflow.keras.layers import Dropout
from tensorflow.keras.optimizers import Adam
from sklearn.model_selection import KFold, cross_val_score
from sklearn.preprocessing import StandardScaler
from statsmodels.tsa.arima.model import ARIMAResults
from statsmodels.tsa.arima.model import ARIMA
from decimal import Decimal
import keras
import kerastuner as kt
from tensorflow.keras.models import save_model
from tensorflow.keras.models import model_from_json
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense
from tensorflow.keras.layers import LSTM
from tensorflow.keras.layers import Dropout
from kerastuner.tuners import RandomSearch
from kerastuner.engine.hyperparameters import HyperParameters
from pickle import dump,load
import logging
logging.getLogger('tensorflow').disabled = True

In [ ]:
path_nav = "/content/drive/MyDrive/Master Thesis/rice_data_customers.csv"
df_nav = pd.read_csv(path_nav)

In [7]:
path_c5 = "/content/drive/MyDrive/Master Thesis/rice_data_c5_full.csv"
df_c5 = pd.read_csv(path_c5)

### Exploring data

In [ ]:
df_c5.head(20)

Unnamed: 0    _ItemNumber MonthYear      Q
0            0   MELCU-6ZSFAV   2022-08    1.0
1            1    MELCU-ALPIB   2022-06   54.0
2            2     CEBWL-SEMI   2022-06    8.0
3            3  BSRAT-20STADB   2022-07    3.0
4            4      CEPIE-SDP   2022-07    4.0
5            5    MELCU-ALPZB   2022-08   12.0
6            6     CEPIE-LLAV   2022-10    2.0
7            7    MELCU-ALPDB   2022-11   18.0
8            8   MELCU-6ZFUNI   2022-08    0.0
9            9      HSJUG-SWW   2022-09    8.0
10          10   MELCU-6ZFUNB   2022-08   13.0
11          11     MELCU-WIFL   2022-08  134.0
12          12      HSJUG-SWW   2022-09   12.0
13          13  MELCU-ALPHEAI   2022-09   12.0
14          14      KICUP-DIN   2022-09   36.0
15          15  MELCP-RECWIFL   2022-06    0.0
16          16    BSHOU-3ZANI   2022-08    2.0
17          17      MELCU-NAB   2022-09   24.0
18          18     THERMO-BIP   2022-09    4.0
19          19    CELPL-EMMIN   2022-09    0.0

In [ ]:
df_c5.columns

Index(['Unnamed: 0', '_ItemNumber', 'MonthYear', 'Q'], dtype='object')

### Descriptive statistics

In [ ]:
###### Descriptive Statistics ###### 
print(f'Length of df: {df.shape[0]} = {df.shape[0]} number of sales')
print('------------------------------------------------------------')
print('Period start:', min(df['Posting Date']))
print('Period end:', max(df['Posting Date']))
print('------------------------------------------------------------')
print('# of items grouped by category:')
print(df["Item Category Code"].value_counts())
print('------------------------------------------------------------')
print('Unique items in dataset:', len(df["Item No_"].unique()))

Length of df: 105532 = 105532 number of sales
------------------------------------------------------------
Period start: 2022-06-11
Period end: 2023-02-09
------------------------------------------------------------
# of items grouped by category:
TABLEWARE     79281
CERAMIC        6688
KITCHEN        5381
HOME           5369
KIDS TABLE     2798
KIDS           2476
STORAGE        1579
BAGS            856
KIDS ROOM       539
ACCESSORIE      422
RICELIFE        143
Name: Item Category Code, dtype: int64
------------------------------------------------------------
Unique items in dataset: 283


### Descriptive visuals

In [ ]:
# Function used
def histogram(df,col):
  '''
  Func: Creating a simple interactive histogram 
  ''' 
  fig = px.histogram(df, x=col, color_discrete_sequence =['#ff5a5f'])
  fig.update_layout(yaxis_title="Count")
  fig.update_layout(title_text=col, title_x=0.5)
  fig.update_layout(plot_bgcolor='rgba(0,0,0,0)')
  fig.show()

In [ ]:
###### Descriptive Visuals ###### 
histogram(df, "Posting Date")

In [ ]:
histogram(df, "Item No_")

In [ ]:
histogram(df, "Item Category Code")

In [ ]:
histogram(df, "Sales Amount (Actual)")

In [ ]:
histogram(df, "Invoiced Quantity")

### Sales vs. time

In [ ]:
def group_df(df):

  df['Posting Date'] = pd.to_datetime(df['Posting Date'])
  df['year'] = df['Posting Date'].dt.year
  df['month'] = df['Posting Date'].dt.month
  df['Date'] = df['year'].astype(str) + '-' + df['month'].apply(lambda x: f'{x:02d}')

  # Drop the original 'date', 'year', and 'month' columns
  df = df.drop(['Posting Date', 'year', 'month'], axis=1) 

  grouped_df = df.groupby(['Date', 'Item No_'])['Invoiced Quantity'].agg('sum')

  grouped_df = grouped_df.reset_index()

  # Making quantity positive
  grouped_df['Invoiced Quantity'] = abs(grouped_df['Invoiced Quantity'])
  
  return grouped_df

grouped_df = group_df(df_c5)

KeyError: ignored

In [ ]:
grouped_df

Date        Item No_  Invoiced Quantity
0     2022-06     BABOX-4ZDIN               26.0
1     2022-06     BGBEA-STRAW               12.0
2     2022-06      BGLEA-RVIL               22.0
3     2022-06      BGLEA-RVIM               11.0
4     2022-06     BGLEA-VIAPL               12.0
...       ...             ...                ...
1648  2023-02      MELCU-SWHE               12.0
1649  2023-02      MELCU-WIFL                0.0
1650  2023-02         MELCU-Y               36.0
1651  2023-02   MELSP-SFAVXCP               48.0
1652  2023-02  MKTBG-SMAGIC21               75.0

[1653 rows x 3 columns]

In [ ]:
def plot_ts(df, x_col, y_col, color_col=None):

    # Set the x-axis and y-axis labels
    x_label = x_col
    y_label = y_col

    # Create the plot using Plotly Express
    fig = px.line(df, x=x_col, y=['abs_y_col'], color=color_col, title=y_col)

    # Customize the plot layout
    fig.update_layout(
        xaxis_title=x_label,
        yaxis_title=y_label,
        hovermode="x unified"
    )

    return fig

In [ ]:
plot_ts(grouped_df, 'Date', 'Invoiced Quantity', color_col = 'Item No_')

In [ ]:
def plot_random_products(df):

    # choose five random items from the data
    unique_items = np.random.choice(df['Item No_'].unique(), 5, replace=False)
    
    # setting subplot structure
    fig = make_subplots(rows=5, cols=1, subplot_titles=unique_items)
    
    # looping throug each of the individual items in the list
    for i, item in enumerate(unique_items): 
        item_df = df[df['Item No_'] == item] # subsetting item data
        fig.add_trace(
            px.line(item_df, x='Date', y='Invoiced Quantity', title=item, template='plotly_white').data[0],
            row=i+1, col=1
        )
        
    # Update layout
    fig.update_layout(
        height=1000,
        title_text='Monthly Sales for 5 Random Products',
        title_x=0.5,
        yaxis=dict(title='Invoiced Quantity'),
        xaxis=dict(title='Date'))

    fig.show()



In [ ]:
plot_random_products(grouped_df)

NameError: ignored

### Forecasting

In [ ]:
test_df=df_c5[df_c5['_ItemNumber'].isin(['BABOX-4ZDIN', 'BGLEA-RVIL', 'BGBEA-STRAW','BGLEA-RVIM'])]

In [ ]:
test_df

Unnamed: 0  _ItemNumber MonthYear     Q
53              53   BGLEA-RVIL   2022-09   1.0
300            300   BGLEA-RVIL   2022-09   4.0
558            558   BGLEA-RVIL   2022-08   1.0
642            642   BGLEA-RVIM   2022-08   4.0
973            973  BABOX-4ZDIN   2022-07  12.0
...            ...          ...       ...   ...
118242      118242   BGLEA-RVIL   2019-01  16.0
118256      118256   BGLEA-RVIM   2016-08   1.0
118282      118282  BABOX-4ZDIN   2021-02  24.0
118315      118315   BGLEA-RVIL   2016-07   8.0
118317      118317   BGLEA-RVIL   2018-09   4.0

[1784 rows x 4 columns]

In [ ]:
test_df = test_df.drop('Unnamed: 0', axis=1)
test_df

_ItemNumber MonthYear     Q
53       BGLEA-RVIL   2022-09   1.0
300      BGLEA-RVIL   2022-09   4.0
558      BGLEA-RVIL   2022-08   1.0
642      BGLEA-RVIM   2022-08   4.0
973     BABOX-4ZDIN   2022-07  12.0
...             ...       ...   ...
118242   BGLEA-RVIL   2019-01  16.0
118256   BGLEA-RVIM   2016-08   1.0
118282  BABOX-4ZDIN   2021-02  24.0
118315   BGLEA-RVIL   2016-07   8.0
118317   BGLEA-RVIL   2018-09   4.0

[1784 rows x 3 columns]

In [ ]:
## Support functions


def lstm_prepros_seq(data, seq=6):
  """
  Function to prepare data for LSTM by converting it into sequential + scaling it
  """
  # Dropping MonthYear since LSTM learns from sequences of past values 
  data = data.drop('MonthYear', axis=1)

  # Initiating minmaxscaler
  scaler = MinMaxScaler()
  data = scaler.fit_transform(data)

  x = []
  y = []

  # looping through the data. The -seq-1 part is to ensure there is enough data points to create an input sequence of length seq AND a corresponding target value
  for i in range(len(data)-seq-1):

    # window = sliding window is breaking the data into smaller, overlapping sequences. Creating windows going from i to i+seq the ,0 indicates selecting the first column
    window = data[i:(i+seq),0]
    x.append(window)
    y.append(data[i+seq,0]) # taking the value after the window of len = seq as y value
  
  return np.array(x), np.array(y), scaler


def plot_sku(df, sku):
  """
  Function for plotting SKU as time series
  """

  df.set_index('MonthYear', inplace=True)
  df['Q'].plot()

  plt.title(f"SKU {sku} sales forecast")
  plt.xlabel("Date")
  plt.ylabel("Sales")
  plt.show()


def model_tuning(hp, train_lstm_x, train_lstm_y):

    """
    Used to hyperparametertune LSTM

    """
    model = Sequential()
    
    # Adding an LSTM layer to the model and testing # of units ranging between a min and a max defined by a step, input shape is defined by the shape of the train data
    model.add(LSTM(hp.Int('input_unit', min_value=32, max_value=512, step=32), return_sequences=True, input_shape=(train_lstm_x.shape[1],train_lstm_x.shape[2])))

    # Loop adding layers to the model
    for i in range(hp.Int('n_layers', 1, 5)):
        model.add(LSTM(hp.Int(f'lstm_{i}_units', min_value=32, max_value=512, step=32),return_sequences=True))
    
    # Final LSTM layer that does not return a sequence like the above (the last LSTM layer should not)
    model.add(LSTM(hp.Int('layer_2_neurons',min_value=32,max_value=512,step=32)))

    # A dropout layer testing different values
    model.add(Dropout(hp.Float('Dropout_rate',min_value=0,max_value=0.5,step=0.1)))

    # A dense layer w 30 neurons choosing between relu and sigmoid
    model.add(Dense(30, activation=hp.Choice('dense_activation',values=['relu', 'sigmoid'],default='relu')))
    model.add(Dense(1, activation=hp.Choice('dense_activation',values=['relu', 'sigmoid'],default='relu')))
   
    model.compile(loss='mean_squared_error', optimizer='adam',metrics = ['mse'])
    
    return model
    

In [ ]:
def forecast(df):

  item_col = '_ItemNumber'
  q = 'Q'
  
  ######### Dictionary creation and initiation #########
  output_dict = {}

  # Looping through each unique SKU in the df
  for sku in df[item_col].unique():

    ######### Initiating outer dict to store specific SKU information #########
    output_dict[sku]={} 

    # Extracting SKU specific df + dropping item_col since its stored in sku_name
    print('************************************')
    print('Processing SKU:', sku)
    print('************************************')
    print('\n')

    # Subsetting SKU information, preprocessing and sorting on MonthYear
    sku_df = df[df[item_col]==sku].drop(item_col, axis=1)
    sku_df['MonthYear'] = pd.to_datetime(sku_df['MonthYear'])
    sku_df = sku_df.groupby('MonthYear').sum().reset_index()
    sku_df = sku_df.sort_values(by='MonthYear')

    # Using epsilon to avoid inf values when converting from Q to pct_change
    epsilon = 1e-8

    # Cross validation using TimeSeriesSplit to make sure we keep the chronological order. For each SKU it will create X splits of the data into training and validation/testing sets.
    n_splits = 2
    tscv = TimeSeriesSplit(n_splits=n_splits)  # random_state=None to produce random splits, if not none, splits will be reproducable like setting a seed. shuffle=False so data is not shuffles before splitting since we are working with timeseries

    ######### XGB PRESET #########
    # Hyperparametergrid
    xgb_params = {
      'learning_rate': [0.01, 0.05, 0.1, 0.2],
      'n_estimators': [10, 20, 30, 40, 50],
      'max_depth':[3,5,8,10],
      'colsample_bytree':[0.3,0.5,0.8]
    }

    # Initiate model regression
    xgboost_model = xgb.XGBRegressor(objective ='reg:squarederror')

    # Define the random search object. Input is: the model, the parameters to search over, the cross-validation method to apply, and what scoring method that evaluates the performance of each set of hyperparameters
    random_search = RandomizedSearchCV(xgboost_model, param_distributions=xgb_params, cv=tscv, scoring='neg_mean_squared_error')


    ######### PROPHET PRESET #########
    proph_params = {
          'seasonality_mode': ['additive', 'multiplicative'],
          'changepoint_prior_scale': [0.01,2],
          'seasonality_prior_scale':[0.01,4],
          'changepoint_range':[0.8,1]
    } 

    ######### LSTM PRESET #########

    # Defining candidate architectures
    
    #Fairly simple model
    mse_list_lstm = []
    models_lstm = []
    

    ######### Metric variables #########
    
    # List for metrics for each fold
    mse_list_arima = []
    mse_list_xgboost = []
    mse_list_prophet = []
    mse_list_lstm = []


    ######### Training and testing #########
    # Looping through train, test splits
    for fold, (train_index, test_index) in enumerate(tscv.split(sku_df)):
      
      num_folds = tscv.get_n_splits()
      
      print(f'FOLD {fold + 1} / {num_folds} ')

      # Split the data into train and test sets for the current fold
      train = sku_df.iloc[train_index]
      test = sku_df.iloc[test_index]

      # Converting Q into % change
      train['Q'] = np.divide(train['Q'] - train['Q'].shift(), train['Q'].shift()+epsilon)
      test['Q'] = np.divide(test['Q'] - test['Q'].shift(), test['Q'].shift()+epsilon)
      
      train = train.dropna()
      test = test.dropna()

      
      ######### ARIMA #########
      print('\n')
      print('************************************')
      print('ARIMA')
      print('************************************')

      train_arima = train.copy()
      test_arima = test.copy()
      
      print('Training model...')
      #Fitting arima model, return and extract the best paramaters
      arima_model = auto_arima(train_arima.set_index('MonthYear').squeeze(), return_best_params = True)

      print('Testing model...')
      # Generate predictions for the test set
      arima_test_predictions = arima_model.predict(n_periods=len(test_arima.set_index('MonthYear').squeeze()))
      
      print('Calculating RMSE...')
      # Calculate the mean squared error on the test set using ARIMA
      arima_mse =  math.sqrt(mean_squared_error(test_arima.set_index('MonthYear').squeeze(), arima_test_predictions))

      mse_list_arima.append(arima_mse)
      print(mse_list_arima)
      
      
      ######### XGBOOST #########
      print('\n')
      print('************************************')
      print('XGBOOST')
      print('************************************')
      
      train_xbg=train.copy()
      test_xbg=test.copy()
      
      # Converting to right date format
      train_xbg['year'] = train_xbg.MonthYear.dt.year
      train_xbg['month'] = train_xbg.MonthYear.dt.month
      
      test_xbg['year'] = test_xbg.MonthYear.dt.year
      test_xbg['month'] = test_xbg.MonthYear.dt.month
      
      xgb_train_x = train_xbg.drop(['Q','MonthYear'], axis=1)
      xgb_train_y = train_xbg['Q']
      
      xgb_test_x = test_xbg.drop(['Q', 'MonthYear'], axis=1)
      xgb_test_y = test_xbg['Q']
      
      print('Training...')
      #Convert the features and labels to DMatrix objects
      dmat_train = xgb.DMatrix(xgb_train_x, label=xgb_train_y)
      dmat_test = xgb.DMatrix(xgb_test_x, label=xgb_test_y)
      
      random_search.fit(xgb_train_x,xgb_train_y)
      best_xgboost_model = random_search.best_estimator_

      print('Testing model...')
      #Generate predictions for the test set
      xgboost_test_predictions = best_xgboost_model.predict(xgb_test_x)
      
      print('Calculating MSE...')
      # Calculate the mean squared error on the test set using the best XGBoost model
      xgboost_mse =  math.sqrt(mean_squared_error(xgb_test_y, xgboost_test_predictions))
      mse_list_xgboost.append(xgboost_mse)
      print(mse_list_xgboost)
      
      
      ######### Prophet #########
      print('\n')
      print('************************************')
      print('PROPHET')
      print('************************************')
      
      train_proph=train.copy()
      test_proph=test.copy()

      # Converting to right date format
      train_proph['MonthYear'] = pd.to_datetime(train_proph['MonthYear'])
      test_proph['MonthYear'] = pd.to_datetime(test_proph['MonthYear'])

      #Ensuring the correct namingconvention
      train_proph = train_proph.rename(columns={"MonthYear": "ds", "Q": "y"})
      test_proph = test_proph.rename(columns={"MonthYear": "ds", "Q": "y"})
      
      # Initiate prophet object
      prophet = Prophet()

      # Initiate object to store best mean squared error
      best_proph_params = None
      best_prophet_mse = float() 

      # Initiate hyperparameter objects to None
      #best_seasonality_mode = None 
      #best_changepoint_prior_scale = None

      for mode in proph_params['seasonality_mode']: # Looping through each mode in the seasonality hp // defining how the seasonal component should be modelled
          for prior_scale in proph_params['changepoint_prior_scale']: # Looping though each scale in the changepoint hp // defining the flexibility of the model. The higher value the less flexible. Flexible = higher ability to fit complex patterns in the training data + more sentitive to changes in data.
              for seasonal_scale in proph_params['seasonality_prior_scale']:
                for changepoint in proph_params['changepoint_range']:
                    print(f'Training with parameters {mode}, {prior_scale}, {seasonal_scale}, {changepoint}...')

                    # Fit Prophet model with the selected hyperparameters
                    prophet_model = Prophet(seasonality_mode=mode, changepoint_prior_scale=prior_scale, seasonality_prior_scale=seasonal_scale,changepoint_range=changepoint)
                    prophet_model.fit(train_proph)
                    
                    print('Testing...')
                    # Generate predictions for the test set (60 mds = 5 Y)
                    future = prophet_model.make_future_dataframe(periods=len(test_proph), freq='MS')
                    future = future[-len(test_proph):] 
                    forecast = prophet_model.predict(future)
                    
                    # Calculate the mean squared error on the test set using Prophet
                    prophet_mse =  math.sqrt(mean_squared_error(test_proph.y, forecast.yhat))
         

                    if best_proph_params is None:
                      best_proph_params = {'mse': prophet_mse, 'seasonality_mode': mode, 'changepoint_prior_scale': prior_scale, 'seasonality_prior_scale': seasonal_scale, 'changepoint_range':changepoint}
                    elif prophet_mse < best_proph_params['mse']:
                      best_proph_params = {'mse': prophet_mse, 'seasonality_mode': mode, 'changepoint_prior_scale': prior_scale, 'seasonality_prior_scale': seasonal_scale, 'changepoint_range':changepoint}
                    elif prophet_mse > best_proph_params['mse']:
                      pass
      
      print('Calculating RMSE...')
      print(best_proph_params['mse'])
      # Store values for the best model on the metrics list
      mse_list_prophet.append(best_proph_params['mse'])
      
      
      ###### LSTM ######
      print('\n')
      print('************************************')
      print('LSTM')
      print('************************************')

      #Making copies of the dataset 
      train_lstm = train.copy()
      test_lstm = test.copy()

      print('Preprocessing data...')
  
      try: 
        
          # Preprocessing input data into sequential seq = 5
          # output is for every 5th (seq size) timestep there will be one y = using 5 prev values to predict next
          train_lstm_x,train_lstm_y,scaler_train = lstm_prepros_seq(train_lstm, 6)
          test_lstm_x,test_lstm_y,scaler_test = lstm_prepros_seq(test_lstm, 6) # applying function
          
          # LSTM requires a 3D shape input (samples, features, timesteps) 
          # samples = number of observations
          # features = 1 (univariate analysis)

          # timesteps = number of timesteps in each sequence so equal to seq parameter
          train_lstm_x = np.reshape(train_lstm_x, (train_lstm_x.shape[0], train_lstm_x.shape[1], 1))
          test_lstm_x = np.reshape(test_lstm_x, (test_lstm_x.shape[0], test_lstm_x.shape[1], 1))

          #train_lstm_y = np.reshape(train_lstm_y, (train_lstm_y.shape[0], 1))
          #test_lstm_y = np.reshape(test_lstm_y, (test_lstm_y.shape[0],1))
          
          # Hyperparametertuning using model_tuning
          tuner = kt.RandomSearch(lambda hp: model_tuning(hp, train_lstm_x, train_lstm_y), objective="mse", max_trials = 4, executions_per_trial =2,directory = "./")

          tuner.search(x=train_lstm_x, y=train_lstm_x, epochs = 10, batch_size =256, validation_data=(test_lstm_x, test_lstm_y))

          best_model = tuner.get_best_models(num_models=1)[0]

          test_pred = best_model.predict(test_lstm_x)
              
          test_pred = scaler_test.inverse_transform(test_pred)
          test_y = scaler_test.inverse_transform([test_lstm_y])
            
          # calculate root mean squared error  
          lstm_mse = math.sqrt(mean_squared_error(test_y[0], test_pred[:,0]))
          print(lstm_mse)

      
      except:

         lstm_mse = -1
         print('IndexError occurred in LSTM model. Skipping this iteration')

    mse_list_lstm.append(lstm_mse)
    #models_lstm.append(model)

    #best_model_idx = np.argmin(mse_list_lstm)
    #lstm_best_params = models_lstm[best_model_idx].get_config()


    
    ###### PRINTING RESULTS ###### 
    plot_sku(sku_df, sku)
    print('\n')
    print('Finalizing results...')
    print('\n')
    print(f'AVERAGE CROSS-VALIDATION SCORES ACROSS {num_folds} FOLDS')
    print('************************************')
    print('\n')
    print('ARIMA')
    mean_mse_arima = sum(mse_list_arima) / len(mse_list_arima)
    print('Mean MSE across folds using ARIMA', mean_mse_arima)
    print('\n')
    print('************************************')
    print('\n')
    print('XGBOOST')
    mean_mse_xgboost = sum(mse_list_xgboost) / len(mse_list_xgboost)
    print('Mean MSE across folds using XGBOOST', mean_mse_xgboost)
    print('\n')
    print('************************************')
    print('\n')
    print('PROPHET')
    mean_mse_prophet = sum(mse_list_prophet) / len(mse_list_prophet)
    print('Mean MSE across folds using PROPHET', mean_mse_prophet)
    print('\n')
    print('************************************')
    print('\n')
    print('LSTM')
    mean_mse_lstm = sum(mse_list_lstm) / len(mse_list_lstm)
    print('Mean MSE across folds using LSTM', mean_mse_lstm)
    print('\n')
    print('************************************')
    print('\n')
    

    print('Appending to dictionary...')
    output_dict[sku]["arima_mse"]=mean_mse_arima
    output_dict[sku]["xgboost_mse"]=mean_mse_xgboost
    output_dict[sku]["prophet_mse"]=mean_mse_prophet
    output_dict[sku]["lstm_mse"]=mean_mse_lstm
    print('\n')
    print('Updated dictionary...')
    print('\n')
    print(output_dict)
    print('\n')
    min_key = min(output_dict[sku], key=lambda x: output_dict[sku][x])
    print(f'Best model based on MSE:{min_key}')
  
  return output_dict

    


    

In [ ]:
dictionary=forecast(test_df)

NameError: ignored

In [ ]:
dictionary

{'BGLEA-RVIL': {'arima_mse': 7.019947810077899,
  'xgboost_mse': 7.1839020078100635,
  'prophet_mse': 7.441011822202384,
  'lstm_mse': 9.012833444504576},
 'BGLEA-RVIM': {'arima_mse': 5.304749195142514,
  'xgboost_mse': 5.300720288964435,
  'prophet_mse': 5.415986035441965,
  'lstm_mse': 8.398389942041222},
 'BABOX-4ZDIN': {'arima_mse': 8.64999179563792,
  'xgboost_mse': 9.808470872504715,
  'prophet_mse': 33.337091672083666,
  'lstm_mse': 9.38165480619287},
 'BGBEA-STRAW': {'arima_mse': 6.352181832756886,
  'xgboost_mse': 5.4190066987462915,
  'prophet_mse': 16.51242016012487,
  'lstm_mse': 3.0748147924957876}}

In [ ]:
def forecast_best_model(performance_dict, df):
    
    forecasts = pd.DataFrame()
    
    for sku, models in performance_dict.items():
        
        sku_df = df[df['_ItemNumber']==sku].drop(['_ItemNumber'], axis=1)

        best_model_name = min(models, key=models.get)
        
        if best_model_name == 'arima_mse':
            print('best model is ARIMA')
            forecast_sales_arima(sku_df)
            
        elif best_model_name == 'xgboost_mse':
            print('best model is XGBOOST')
        elif best_model_name == 'prophet_mse':
            print('best model is Prophet')
        elif best_model_name == 'lstm_mse':
            print('best model is LSTM')
        else:
          raise ValueError('Invalid model name')
       

In [ ]:
forecast_best_model(dictionary, test_df)

best model is ARIMA


ValueError: ignored

In [ ]:
from sklearn.model_selection import TimeSeriesSplit

def forecast_sales_arima(data, forecast_len=5, window_size=12):
    
    # Initialize time series split
    tscv = TimeSeriesSplit(n_splits=None, max_train_size=window_size)
    
    # Initialize lists to store forecasts and performance metrics
    all_forecasts = []
    all_conf_ints = []
    all_metrics = []
    
    # Iterate over the splits
    for train_index, test_index in tscv.split(data):
        
        # Get the train and test sets
        train = data.iloc[train_index]
        test = data.iloc[test_index]
        
        # Fit ARIMA model using auto_arima function
        model = auto_arima(train,
                           seasonal=False, 
                           error_action='ignore', 
                           suppress_warnings=True, 
                           stepwise=True)
        
        # Predict test set
        forecasts, conf_int = model.predict(forecast_len, return_conf_int=True, alpha=0.05)
        
        # Compute performance metrics
        mae = np.mean(np.abs(forecasts - test))
        mse = np.mean((forecasts - test) ** 2)
        
        # Append forecasts and metrics to lists
        all_forecasts.append(forecasts)
        all_conf_ints.append(conf_int)
        all_metrics.append({'MAE': mae, 'MSE': mse})
    
    # Convert forecasts and metrics to arrays
    all_forecasts = np.concatenate(all_forecasts)
    all_conf_ints = np.concatenate(all_conf_ints, axis=0)
    all_metrics = {k: [d[k] for d in all_metrics] for k in all_metrics[0]}
    
    # Compute overall performance metrics
    overall_mae = np.mean(np.abs(all_forecasts - data[-len(all_forecasts):]))
    overall_mse = np.mean((all_forecasts - data[-len(all_forecasts):]) ** 2)
    
    # Plot forecasts and confidence intervals
    plt.figure(figsize=(12,6))
    plt.plot(data.index[:-forecast_len], data[:-forecast_len], label='train')
    plt.plot(data.index[-len(all_forecasts):], all_forecasts, label='forecast')
    plt.fill_between(data.index[-len(all_forecasts):], all_conf_ints[:,0], all_conf_ints[:,1], alpha=0.2)
    plt.legend()
    plt.show()
    
    # Return forecasted sales value and model parameters
    return (all_forecasts, all_conf_ints), {'p': model.order[0], 'd': model.order[1], 'q': model.order[2]}, {'MAE': overall_mae, 'MSE': overall_mse, 'split_metrics': all_metrics}



In [ ]:
sku_df=df_c5[df_c5['_ItemNumber'].isin(['BABOX-4ZDIN'])]

In [ ]:
sku_df

Unnamed: 0  _ItemNumber MonthYear     Q
973            973  BABOX-4ZDIN   2022-07  12.0
1076          1076  BABOX-4ZDIN   2022-09  12.0
1599          1599  BABOX-4ZDIN   2022-07   1.0
1705          1705  BABOX-4ZDIN   2022-09   3.0
2239          2239  BABOX-4ZDIN   2022-06   1.0
...            ...          ...       ...   ...
116873      116873  BABOX-4ZDIN   2022-01   1.0
117299      117299  BABOX-4ZDIN   2021-09  18.0
117910      117910  BABOX-4ZDIN   2022-03   6.0
118084      118084  BABOX-4ZDIN   2021-08  12.0
118282      118282  BABOX-4ZDIN   2021-02  24.0

[266 rows x 4 columns]

In [ ]:
forecast_sales(sku_df)

ValueError: ignored